In [ ]:
import matplotlib
%matplotlib inline
import matplotlib.pyplot as plt
import numpy
import os
import datetime
import scipy
from numpy.random import randn
import pyproj


import numpy as np
from netCDF4 import Dataset, chartostring, date2num, num2date, default_fillvals
import pyproj

import pickle
from scipy.interpolate import RegularGridInterpolator

from IPython.core.display import display, HTML
display(HTML("<style>.container { width:100% !important; }</style>"))

## Read SWIM L2S spectral data

In [ ]:
prod = '20231122T164833_20231122T174627_1.0.2'
beam = '08'
l2s_path = '/media/drfab/data/cfosat/swi_l2s___/v1/CFO_OP06_SWI_L2S____F_'+prod+'/CFO_OP06_SWI_L2S'+beam+'__F_'+prod+'.nc'
clon = -146.8 # Nov 22 2023 storm pacific
clat = 40

prod = '20240217T081133_20240217T094440_1.0.2'
beam = '10'
l2s_path = '/media/drfab/data/cfosat/swi_l2s___/v1/CFO_OP06_SWI_L2S____F_'+prod+'/CFO_OP06_SWI_L2S'+beam+'__F_'+prod+'.nc'
clon = -22.8
clat = 24.6 # North Atlantic storm

dset = Dataset(l2s_path, 'r')

fluct_specs = dset.variables['fluctuation_spectra'][:]
wave_spec = dset.variables['wave_spectra'][:]
seg_sea_ice_concentration = dset.variables['seg_sea_ice_concentration'][:]
klin = dset.variables['klin'][:]
near_lat = dset.variables['near_lat'][:]
near_lon = dset.variables['near_lon'][:]
far_lat = dset.variables['far_lat'][:]
far_lon = dset.variables['far_lon'][:]
lat = dset.variables['lat'][:]
lon = dset.variables['lon'][:]
time = dset.variables['time'][:]

dr = abs(lon-clon)+abs(lat-clat)
deb = np.argmin(dr)-200
fin = np.argmin(dr)+200

#sigma0 = db2linear(dset.variables['sigma0'][:])
sigma0 = (dset.variables['sigma0'][:])
sigma0_nv = dset.variables['sigma0_nv'][:]
#sigma0_trend = db2linear(dset.variables['sigma0_trend'][:])
# sigma0_trend = (dset.variables['sigma0_trend'][:])
# sigma0 = sigma0 /sigma0_trend

seg_flag = dset.variables['seg_flag'][:]

phi = dset.variables['phi'][:]
phi_geo = dset.variables['phi_geo'][:]

klin = dset.variables['klin'][:]
k = dset.variables['k'][:]
dk = dset.variables['dk'][:]

inc = dset.variables['incidence'][:]
l2s_inc = dset.l2s_angle

u10 = dset.variables['seg_model_u10'][:].mean(axis=1)
v10 = dset.variables['seg_model_v10'][:].mean(axis=1)
wind = np.sqrt(u10**2+v10**2)

mtf = dset.variables['mtf'][:].mean(axis=1)

partition_label = dset.variables['partition_label'][:]
partition_wavelength = dset.variables['partition_wavelength'][:]
partition_direction = dset.variables['partition_direction'][:]
partition_lon = dset.variables['partition_lon'][:]
partition_lat = dset.variables['partition_lat'][:]
ptime =  dset.variables['partition_time'][:]
partition_hs = dset.variables['partition_hs'][:]
tcs = dset.getncattr('time_coverage_start')
tce = dset.getncattr('time_coverage_end')

# srt = ptime.argsort()

# partition_lon = partition_lon[srt]
# partition_lat = partition_lat[srt]
# partition_direction = partition_direction[srt]
# partition_wavelength = partition_wavelength[srt]
# partition_hs = partition_hs[srt]

drpart = abs(partition_lon-clon)+abs(partition_lat-clat)
npart0 = np.argmin(drpart)-100

dset.close()

fluct_spec = fluct_specs.mean(axis=-1)

#sli = slice(deb,fin)#lat.shape[0]

sli = slice(deb,fin)

In [ ]:
fig = plt.figure(figsize = (20,10))
w = np.where(partition_wavelength>40)
plt.plot(partition_lat[w],partition_wavelength[w],'.')
plt.grid()

In [ ]:
_nk = 28 # fluc_spec
print(klin[_nk - 1], 2. * np.pi / klin[_nk - 1])
_lat = np.zeros((fluct_spec[sli, :].shape[0], _nk))
_lon = np.zeros((fluct_spec[sli, :].shape[0], _nk))
_lat1 =  np.zeros((fluct_spec[sli, :].shape[0], _nk))
_lat2 =  np.zeros((fluct_spec[sli, :].shape[0], _nk))
_lon1 =  np.zeros((fluct_spec[sli, :].shape[0], _nk))
_lon2 =  np.zeros((fluct_spec[sli, :].shape[0], _nk))

geod= pyproj.Geod(ellps='WGS84')
for i in range(_lat.shape[0]):
    az,back_azimuth,dist = geod.inv(near_lon[sli][i], near_lat[sli][i], far_lon[sli][i], far_lat[sli][i])
    endlon, endlat, backaz = geod.fwd(near_lon[sli][i], near_lat[sli][i], az+90, dist/60)
    dlon = endlon - near_lon[sli][i]
    dlat = endlat - near_lat[sli][i]
    ll = geod.npts(near_lon[sli][i], near_lat[sli][i], far_lon[sli][i], far_lat[sli][i], npts=_nk)
    _lat[i, :] = np.array(ll)[:, 1]
    _lon[i, :] = np.array(ll)[:, 0]
    ll1 = geod.npts(near_lon[sli][i]-dlon, near_lat[sli][i]-dlat, far_lon[sli][i]-dlon, far_lat[sli][i]-dlat, npts=_nk)
    _lat1[i, :] = np.array(ll1)[:, 1]
    _lon1[i, :] = np.array(ll1)[:, 0]    
    ll2 = geod.npts(near_lon[sli][i]+dlon, near_lat[sli][i]+dlat, far_lon[sli][i]+dlon, far_lat[sli][i]+dlat, npts=_nk)
    _lat2[i, :] = np.array(ll2)[:, 1]
    _lon2[i, :] = np.array(ll2)[:, 0]

In [ ]:
def remove_low_freq(spec, ikstart):
    nphi, nk = spec.shape
    ikstop = np.zeros(nphi, dtype='int32') + ikstart
    for ik in range(ikstart, nk - 2):
        ind = np.where(ikstop == ik)[0]
        if ind.size == 0:
            break
        lowf = spec[ind, ik] > spec[ind, ik + 1]
        if lowf.min() == False:
            indnl = ind[~lowf]
            spec[indnl, 0:ik + 1] = 0
        if lowf.max() == True:
            indl = ind[lowf]
            ikstop[indl] = ik + 1
    return spec


# Remove low freq
ikstart = np.where(klin <= 2. * np.pi / 1000.)[0][-1]
flsp = remove_low_freq(fluct_spec[deb:deb+_lat.shape[0]-1, :], ikstart)

In [ ]:
def compute_klog(kmin, kmax, nklog):
    alpha = (kmax / kmin) ** (1. / (nklog - 1.))
    klog = kmin * alpha ** np.arange(nklog)
    dklog = (np.sqrt(alpha) - 1. / np.sqrt(alpha)) * klog
    return klog, dklog

nklog = 60
klow = 0.00628318530718
khigh = 0.209439510239

klog, dklog = compute_klog(klow, khigh, nklog)

dklin = klin[1] - klin[0]


from SEAScope.lib.utils import create_collection, init_ids
from SEAScope.lib.utils import create_granule
import SEAScope.upload
from SEAScope.lib.utils import set_field
from SEAScope.lib.utils import create_variable
collection_id, collection = create_collection('CFOSAT SWIM spectral v1.0')
# IP address and port used to reach the SEAScope standalone application
host = '127.0.0.1'
port = 11155
with SEAScope.upload.connect(host, port) as link:
# Send create collection job
    SEAScope.upload.collection(link, collection)
    
with SEAScope.upload.connect(host, port) as link:   
    for i in range(_lat.shape[0]):
        gcps = []
        gcps1 = []
        gcps2 = []
        count = 0
        for j in range(_nk):
            gcp = {'lon': _lon[i,j], 'lat': _lat[i,j], 'i': i, 'j': j}
            gcp1 = {'lon': _lon1[i,j], 'lat': _lat1[i,j], 'i': i, 'j': j}
            gcp2 = {'lon': _lon2[i,j], 'lat': _lat2[i,j], 'i': i, 'j': j}
            if _lat[i,j] != 0:
                gcps.append(gcp)
                gcps1.append(gcp1)
                gcps2.append(gcp2)
                count=count+1

        # Create granule
        start_dt = datetime.datetime.strptime(tcs, "%Y-%m-%dT%H:%M:%SZ")
        stop_dt = datetime.datetime.strptime(tce, "%Y-%m-%dT%H:%M:%SZ")
        granule_id, granule = create_granule(collection_id, gcps, start_dt, stop_dt)
        granule_id1, granule1 = create_granule(collection_id, gcps1, start_dt, stop_dt)
        granule_id2, granule2 = create_granule(collection_id, gcps2, start_dt, stop_dt)

        # Set variables
        # Enter a name for each variable field
        from SEAScope.lib.utils import set_field
        field_name_time = beam+' deg fluc spec swell v1'
        set_field(granule, field_name_time, fluct_spec[deb+i, 0:_nk])
        SEAScope.upload.granule(link, granule)
        set_field(granule1, field_name_time, fluct_spec[deb+i, 0:_nk])
        SEAScope.upload.granule(link, granule1)
        set_field(granule2, field_name_time, fluct_spec[deb+i, 0:_nk])
        SEAScope.upload.granule(link, granule2)
#         field_name_time = beam+' deg wave spec swell'
# #         field_name_time = beam+' deg partition index'
#         set_field(granule, field_name_time, wave_spec[deb+i, 0:_nk])
#         set_field(granule, field_name_time, partition_label[deb+i, 0:_nk])
        
        # Send create granule job    
# Create a variable for each parameter
variable_name_time = field_name_time
var1 = create_variable(collection, variable_name_time, [field_name_time], dims=1)

# Upload to SEAScope
with SEAScope.upload.connect(host, port) as link:
    # Send create variable jobs
    SEAScope.upload.variable(link, var1)
    
# Rendering configuration for hs
rcfg1 = var1['rendering']
rcfg1['min'] = 0
rcfg1['max'] = 0.2 #for fluct spec
rcfg1['colormap'] = 'jet'
rcfg1['color'] = [255,255,255]
rcfg1['opacity'] = 1
rcfg1['zindex'] = .923

# Upload to SEAScope
with SEAScope.upload.connect(host, port) as link:
    # Send create rendering config jobs
    SEAScope.upload.rendering_config(link, rcfg1)

In [ ]:

from SEAScope.lib.utils import create_collection, init_ids
from SEAScope.lib.utils import create_granule
import SEAScope.upload
from SEAScope.lib.utils import set_field
from SEAScope.lib.utils import create_variable
collection_id, collection = create_collection('CFOSAT SWIM spectral v1.0')
# IP address and port used to reach the SEAScope standalone application
host = '127.0.0.1'
port = 11155
with SEAScope.upload.connect(host, port) as link:
# Send create collection job
    SEAScope.upload.collection(link, collection)
    
with SEAScope.upload.connect(host, port) as link:   
    for i in range(_lat.shape[0]):
        nt = [3, 6, 13, 26]
        for j in range(4):
            gcps = []
            az,back_azimuth,dist = geod.inv(_lon[i,nt[j]], _lat[i,nt[j]], _lon[i,nt[j]+1], _lat[i,nt[j]+1])
            endlon, endlat, backaz = geod.fwd(_lon[i,nt[j]], _lat[i,nt[j]], az+90, dist/2)
            dlon = endlon - _lon[i,nt[j]]
            dlat = endlat - _lat[i,nt[j]]
            gcp1 = {'lon': _lon[i,nt[j]]-dlon, 'lat': _lat[i,nt[j]]-dlat, 'i': i, 'j': 0}
            gcp2 = {'lon': _lon[i,nt[j]]+dlon, 'lat': _lat[i,nt[j]]+dlat, 'i': i, 'j': 1}
            if _lat[i,j] != 0:
                gcps.append(gcp1)
                gcps.append(gcp2)

        # Create granule
            start_dt = datetime.datetime.strptime(tcs, "%Y-%m-%dT%H:%M:%SZ")
            stop_dt = datetime.datetime.strptime(tce, "%Y-%m-%dT%H:%M:%SZ")
            granule_id, granule = create_granule(collection_id, gcps, start_dt, stop_dt)

        # Set variables
        # Enter a name for each variable field
            from SEAScope.lib.utils import set_field
            field_name_time = beam+' wavenumber ticks'
            set_field(granule, field_name_time,np.ones(2))
#         field_name_time = beam+' deg wave spec swell'
# #         field_name_time = beam+' deg partition index'
#         set_field(granule, field_name_time, wave_spec[deb+i, 0:_nk])
#         set_field(granule, field_name_time, partition_label[deb+i, 0:_nk])
        
        # Send create granule job
            SEAScope.upload.granule(link, granule)
    
# Create a variable for each parameter
variable_name_time = field_name_time
var1 = create_variable(collection, variable_name_time, [field_name_time], dims=1)

# Upload to SEAScope
with SEAScope.upload.connect(host, port) as link:
    # Send create variable jobs
    SEAScope.upload.variable(link, var1)
    
# Rendering configuration for hs
rcfg1 = var1['rendering']
rcfg1['min'] = 1
rcfg1['max'] = 1 #for fluct spec
rcfg1['colormap'] = ''
rcfg1['color'] = [255,255,255]
rcfg1['opacity'] = 0.5
rcfg1['zindex'] = .953

# Upload to SEAScope
with SEAScope.upload.connect(host, port) as link:
    # Send create rendering config jobs
    SEAScope.upload.rendering_config(link, rcfg1)

## Load and select data from SEAScope
<span style="color:green">**Select the surface velocity from cmems 008 046 you want to play with (current streamlines)**<br>
**Draw a polygon on SEASCope**<br>
**Click on the extract button on the polygon window**<br>
</span>


In [ ]:
# Load data directly from viewer memory
from SEAScope.lib import get_extracted_data
extractions = get_extracted_data()
## Print a list of path of extracted granules 
print('\n'.join(extractions.keys()))
# Get longitudes, latitudes from gcps and time from first granule
granule_uri =  next( v for i, v in enumerate(extractions.keys()) if i == 0)
extraction = extractions[granule_uri]
start = extraction['meta']['start']
print(extraction['meta']['fields'])


In [ ]:
name_var_u = 'ugos'
name_var_v = 'vgos'

extraction = extractions[granule_uri]   
u = extraction['data'][name_var_u]
v = extraction['data'][name_var_v]

from SEAScope.lib.utils import get_lonlat
lon2D, lat2D = get_lonlat(extraction, numpy.shape(u))


In [ ]:
# npart0 = 180 # for 8/10 deg beam
# npart0 = 130 # for 6 deg beam
# npart0 = 180 # for 4 deg beam
# npart0 = 220 # for 2 deg beam
npartitions = 160


def ev(var, x, y):
    if numpy.isnan(x) or numpy.isnan(y):
        return numpy.nan
    nx, ny = numpy.shape(var)
    i = int(x)
    j = int(y)
    if (i > nx - 2) or (j > ny - 2):
        return numpy.nan
    dx = x - i
    dy = y - j
    uix = dx * var[i + 1, j] + (1 - dx) * var[i, j]
    uiy = dx * var[i + 1, j + 1] + (1 - dx) * var[i, j + 1]
    ui = dy * uiy + (1 - dy) * uix
    return ui


# Initialize wave ray position with SWIM partitions

granule_id = None
# Time step for advection (in sec)
s=1
dt = 3600/3/s
# Number of seeds
nseed = npartitions
# Wave number

# Total time of advection 
nstep = int(20*s) #! Change this

tmpu = extraction['data'][name_var_u]
tmpv = extraction['data'][name_var_v]
#urand = numpy.multiply(tmpu,0.02*randn(u.shape[0],u.shape[1]))
#vrand = numpy.multiply(tmpv,0.02*randn(u.shape[0],u.shape[1]))
#urand = 0.05*randn(u.shape[0],u.shape[1])
#vrand = 0.05*randn(u.shape[0],u.shape[1])
res = (lat2D[int(u.shape[0]/2+1), int(u.shape[1]/2)]
       -lat2D[int(u.shape[0]/2), int(u.shape[1]/2)]) * 100000
x = numpy.full((nstep+1, nseed), numpy.nan)
y = numpy.full((nstep+1, nseed), numpy.nan)
lon = numpy.full((nstep+1, nseed), numpy.nan)
lat = numpy.full((nstep+1, nseed), numpy.nan)
for c in range(nseed):
    wl = partition_wavelength[npart0+c]
    k = 2*numpy.pi/wl
    # Wave direction in radians
    tetap = partition_direction[npart0+c]
    if partition_direction[npart0+c] > 180 :
        tetap = partition_direction[npart0+c]-180
    tetad = 90-tetap # clockwise from north
    teta0 = tetad*numpy.pi/180
    dd = np.abs(lon2D-partition_lon[npart0+c])+np.abs(lat2D-partition_lat[npart0+c])
    x[0,c] = np.unravel_index(np.argmin(dd, axis=None), dd.shape)[0]-u.shape[0]
    y[0,c] = np.unravel_index(np.argmin(dd, axis=None), dd.shape)[1]
    lon[0,c] = ev(lon2D, x[0,c], y[0,c])
    lat[0,c] = ev(lat2D, x[0,c], y[0,c])
    teta = teta0
    kx = k*numpy.sin(teta)
    ky = k*numpy.cos(teta)
    for i in range(nstep):
        u = tmpu#+urand
        v = tmpv#+vrand
        if x[i, c] is numpy.ma.masked or y[i, c] is numpy.ma.masked:
            continue
#        if (x[i, c]>(u.shape[0]-1)) or (y[i, c]>(u.shape[1]-1)):
#            continue
#        if (x[i, c]<0) or (y[i, c]<0):
#            continue
        omega = numpy.sqrt(9.81*(kx**2+ky**2)) + (ky*ev(u,x[i,c],y[i,c])
                            +kx*ev(v,x[i,c],y[i,c]))
        dx = dt*(ev(v,x[i,c],y[i,c])+numpy.sqrt(9.81/(numpy.sqrt(kx**2+ky**2)))
                 *numpy.sin(teta)/2)/res
        dy = dt*(ev(u,x[i,c],y[i,c])+numpy.sqrt(9.81/(numpy.sqrt(kx**2+ky**2)))
                 *numpy.cos(teta))/2/res
        teta = numpy.arctan2(kx,ky)
        if dx is numpy.ma.masked or dy is numpy.ma.masked:
            continue
        if (x[i, c]+dx<(1-u.shape[0])) or (y[i, c]+dy>(u.shape[1]-1)):
            continue
        if (x[i, c]+dx>0) or (y[i, c]+dy<0):
            continue
        domegax = omega - (numpy.sqrt(9.81*(kx**2+ky**2))
                           + (ky*ev(u,x[i,c]+dx,y[i,c])
                           + kx*ev(v,x[i,c]+dx,y[i,c])))
        domegay = omega - (numpy.sqrt(9.81*(kx**2+ky**2))
                           + (ky*ev(u,x[i,c],y[i,c]+dy)
                           + kx*ev(v,x[i,c],y[i,c]+dy)))

        x[i+1,c] = x[i,c] + dx
        y[i+1,c] = y[i,c] + dy
        lon[i+1,c] = ev(lon2D, x[i+1,c], y[i+1,c])
        lat[i+1,c] = ev(lat2D, x[i+1,c], y[i+1,c])
        dkx = dt*domegax/dx/res
        dky = dt*domegay/dy/res
        kx = kx + dkx
        ky = ky + dky

In [ ]:
from SEAScope.lib.utils import create_collection, init_ids
# Make sure to keep the collection identifier, we will need it later
collection_id, collection = create_collection('CFOSAT SWIM Simulated wave rays')
print(collection_id)

# IP address and port used to reach the SEAScope standalone application
host = '127.0.0.1'
port = 11155

import SEAScope.upload
with SEAScope.upload.connect(host, port) as link:
# Send create collection job
    SEAScope.upload.collection(link, collection)
    
from SEAScope.lib.utils import create_granule
# Shell of Granule
# Each position of the trajectory will be used as GCP
with SEAScope.upload.connect(host, port) as link:   
    for c in range(nseed):
        if partition_wavelength[npart0+c] < 500:
            continue
        if partition_wavelength[npart0+c] > 1000:
            continue
        gcps = []
        count = 0
        for i in range(0, nstep+1):
            gcp = {'lon': lon[i,c], 'lat': lat[i,c], 'i': i, 'j': 0}
            if lat[i,c] != 0:
                gcps.append(gcp)
                count=count+1

        # Create granule
        start_dt = datetime.datetime.strptime(tcs, "%Y-%m-%dT%H:%M:%SZ")
        stop_dt = datetime.datetime.strptime(tce, "%Y-%m-%dT%H:%M:%SZ")
        granule_id, granule = create_granule(collection_id, gcps, start_dt, stop_dt)

        # Set variables
        # Enter a name for each variable field
        from SEAScope.lib.utils import set_field
        field_name_time ='wavelength'
        set_field(granule, field_name_time, numpy.arange(count)*dt/3600*0+partition_wavelength[npart0+c])
#         field_name_time ='hs'
#         set_field(granule, field_name_time, numpy.arange(count)*dt/3600*0+partition_hs[npart0+c])
        
        # Send create granule job
        SEAScope.upload.granule(link, granule)
        
from SEAScope.lib.utils import create_variable

# Create a variable for each parameter
variable_name_time = 'wavelength '+beam+' backward'
# variable_name_time = 'hs'
var1 = create_variable(collection, variable_name_time, [field_name_time], dims=1)

# Upload to SEAScope
with SEAScope.upload.connect(host, port) as link:
    # Send create variable jobs
    SEAScope.upload.variable(link, var1)
    
# Rendering configuration for the time
rcfg1 = var1['rendering']
rcfg1['min'] = 500
rcfg1['max'] = 900
# rcfg1['min'] = 0
# rcfg1['max'] = 3
rcfg1['colormap'] = 'jet'
rcfg1['color'] = [255,255,255]
rcfg1['opacity'] = 1
rcfg1['zindex'] = .923

# Upload to SEAScope
with SEAScope.upload.connect(host, port) as link:
    # Send create rendering config jobs
    SEAScope.upload.rendering_config(link, rcfg1)

In [ ]:
from SEAScope.lib.utils import create_collection, init_ids
# Make sure to keep the collection identifier, we will need it later
collection_id, collection = create_collection('CFOSAT SWIM Simulated wave rays')
print(collection_id)

# IP address and port used to reach the SEAScope standalone application
host = '127.0.0.1'
port = 11155

import SEAScope.upload
with SEAScope.upload.connect(host, port) as link:
# Send create collection job
    SEAScope.upload.collection(link, collection)
    
from SEAScope.lib.utils import create_granule
# Shell of Granule
# Each position of the trajectory will be used as GCP
with SEAScope.upload.connect(host, port) as link:   
    for c in range(nseed):
        if partition_wavelength[npart0+c] < 500:
            continue
        if partition_wavelength[npart0+c] > 1000:
            continue
        gcps = []
        count = 0
        for i in range(0, nstep+1):
            gcp = {'lon': lon[i,c], 'lat': lat[i,c], 'i': i, 'j': 0}
            if lat[i,c] != 0:
                gcps.append(gcp)
                count=count+1

        # Create granule
        start_dt = datetime.datetime.strptime(tcs, "%Y-%m-%dT%H:%M:%SZ")
        stop_dt = datetime.datetime.strptime(tce, "%Y-%m-%dT%H:%M:%SZ")
        granule_id, granule = create_granule(collection_id, gcps, start_dt, stop_dt)

        # Set variables
        # Enter a name for each variable field
        from SEAScope.lib.utils import set_field
        field_name_time ='hs'
        set_field(granule, field_name_time, numpy.arange(count)*dt/3600*0+partition_hs[npart0+c])
        
        # Send create granule job
        SEAScope.upload.granule(link, granule)
        
from SEAScope.lib.utils import create_variable

# Create a variable for each parameter
# variable_name_time = 'wavelength '+beam+' backward'
variable_name_time = 'hs '+beam
var1 = create_variable(collection, variable_name_time, [field_name_time], dims=1)

# Upload to SEAScope
with SEAScope.upload.connect(host, port) as link:
    # Send create variable jobs
    SEAScope.upload.variable(link, var1)
    
# Rendering configuration for the time
rcfg1 = var1['rendering']
# rcfg1['min'] = 500
# rcfg1['max'] = 800
rcfg1['min'] = 0
rcfg1['max'] = 3
rcfg1['colormap'] = 'jet'
rcfg1['color'] = [255,255,255]
rcfg1['opacity'] = 1
rcfg1['zindex'] = .923

# Upload to SEAScope
with SEAScope.upload.connect(host, port) as link:
    # Send create rendering config jobs
    SEAScope.upload.rendering_config(link, rcfg1)